In [1]:
import numpy as np
import matplotlib.pyplot as plt
import scipy.optimize as sco
import pandas as pd
pd.options.plotting.backend = "plotly"
import plotly.graph_objects as go

In [2]:
def rand_weights(n):
    k = np.random.rand(n)
    return k /sum(k)

In [3]:
def random_portfolio(mean_returns,cov_returns,risk_free_rate = 0.0): #returns has to be DataFrame
    p = np.asmatrix(mean_returns)
    w = np.asmatrix(rand_weights(mean_returns.shape[0]))
    C = np.asmatrix(cov_returns)

    mu = w*p.T
    sigma = np.sqrt(w*C*w.T)

    if sigma >0.5:
        return random_portfolio(returns)
    return float(mu),float(sigma), float((mu-risk_free_rate)/sigma)

def performance_portfolio(weights,mean_returns,cov_returns,risk_free_rate=0):
    p = np.asmatrix(mean_returns)
    w = np.asmatrix(weights)
    C = np.asmatrix(cov_returns)

    mu = w*p.T
    sigma = np.sqrt(w*C*w.T)
    return float(mu), float(sigma), float((mu-risk_free_rate)/sigma)

In [4]:
def neg_sharpe_ratio(weights,mean_returns,cov_returns,risk_free_rate=0):
    p_ret, p_std, p_sharpe = performance_portfolio(weights,mean_returns,cov_returns,risk_free_rate)
    return -(p_sharpe)

def max_sharpe_ratio(mean_returns,cov_returns,risk_free_rate = 0.03):
    n_assets    = len(mean_returns)
    args        = (mean_returns,cov_returns,risk_free_rate)
    constraints = ({'type': 'eq', 'fun': lambda x: np.sum(x) - 1})
    bound       = (0.0,1.0)
    bounds      = tuple(bound for asset in range(n_assets))
    results     = sco.minimize(neg_sharpe_ratio, n_assets*[1./n_assets,],
                               args = args, method = 'SLSQP', 
                               bounds = bounds, constraints = constraints)
    return results['x']

In [5]:
def neg_rentability(weights,mean_returns,cov_returns,risk_free_rate=0):
    p_ret, p_std, p_sharpe = performance_portfolio(weights,mean_returns,cov_returns,risk_free_rate)
    return -(p_ret)

def max_rentability(mean_returns,cov_returns,risk_free_rate = 0.03):
    n_assets    = len(mean_returns)
    args        = (mean_returns,cov_returns,risk_free_rate)
    constraints = ({'type': 'eq', 'fun': lambda x: np.sum(x) - 1})
    bound       = (0.0,1.0)
    bounds      = tuple(bound for asset in range(n_assets))
    results     = sco.minimize(neg_rentability, n_assets*[1./n_assets,],
                               args = args, method = 'SLSQP', 
                               bounds = bounds, constraints = constraints)
    return results['x']

In [6]:
def portfolio_volatility(weights,mean_returns,cov_returns):
    return performance_portfolio(weights,mean_returns,cov_returns)[1]

def min_variance(mean_returns,cov_returns):
    num_assets  = len(mean_returns)
    args        = (mean_returns,cov_returns)
    constraints = ({'type':'eq','fun':lambda x: np.sum(x)-1})
    bound       = (0.0,1.0)
    bounds      = tuple(bound for asset in range(num_assets))
    
    results     = sco.minimize(portfolio_volatility, num_assets*[1./num_assets,],
                              args = args, method = 'SLSQP',
                              bounds = bounds, constraints = constraints)
    return results['x']

In [7]:
def target_return(mean_returns,cov_returns,target,risk_free_rate): #for a given return return weithgs of min volatility
    num_assets = len(mean_returns)
    args       = (mean_returns, cov_returns)
    def portfolio_return(weights):
        return performance_portfolio(weights, mean_returns, cov_returns, risk_free_rate)[0]
    
    constraints = ({'type': 'eq', 'fun': lambda x: portfolio_return(x) - target},
                   {'type': 'eq', 'fun': lambda x: np.sum(x) - 1})
    bounds = tuple((0,1) for asset in range(num_assets))
    results = sco.minimize(portfolio_volatility,
                          num_assets*[1./num_assets,], args=args, 
                          method='SLSQP', bounds=bounds, 
                          constraints=constraints)
    return results['x']

def efficient_frontier(mean_returns,cov_returns,returns_range):
    efficients = []
    for ret in returns_range:
        efficients.append(target_return(mean_returns,
                                           cov_returns,ret,risk_free_rate))
    return efficients

In [8]:
df = pd.read_excel("Valores Cuota.xlsx")

prices = df.set_index(df.columns[0])

names = prices.columns
graph_price = prices.plot(title = "Price Assets vs. Time")
graph_price.show()

risk_free_rate = 3/100

In [9]:
returns = np.log(prices.pct_change()+1)*-1
returns = returns.resample("Y").sum()
mean_returns = returns.mean()
std_returns  = returns.std()
cov_returns = returns.cov()


mean_std = pd.concat([mean_returns, std_returns],axis = 1)*100
mean_std.columns =["mean returns","std returns/risk"]
#returns.to_excel("retornos.xlsx")
graph_ret_std = mean_std.plot.bar(barmode = 'group',title = "Mean returns vs. risk")
#graph_ret_std

In [10]:
returns_monthly = returns.resample("Y").sum()*100
graph_returns = returns_monthly.plot.bar(barmode = "group")
#graph_returns.show()

In [11]:
n_portfolios = 10000

np.random.seed(3)
others_means , others_stds, others_sharpe = np.column_stack(
                                                        [random_portfolio(mean_returns,cov_returns,risk_free_rate) 
                                                        for i in np.arange(n_portfolios)])

other_portfolios = pd.concat([pd.DataFrame(others_means),pd.DataFrame(others_stds),
                              pd.DataFrame(others_sharpe)],axis = 1)
other_portfolios.columns = ["retorns","risk","Isharpe"]
other_portfolios["Type"]= "Others"
other_portfolios["weights"] = np.nan
other_portfolios

retorns      risk   Isharpe    Type  weights
0     0.074732  0.074255  0.602413  Others      NaN
1     0.078032  0.103809  0.462692  Others      NaN
2     0.073370  0.059368  0.730528  Others      NaN
3     0.076414  0.082201  0.564646  Others      NaN
4     0.075304  0.079520  0.569715  Others      NaN
...        ...       ...       ...     ...      ...
9995  0.074709  0.070475  0.634396  Others      NaN
9996  0.075577  0.077406  0.588801  Others      NaN
9997  0.077362  0.094642  0.500432  Others      NaN
9998  0.075668  0.078350  0.582868  Others      NaN
9999  0.076272  0.091684  0.504690  Others      NaN

[10000 rows x 5 columns]

In [12]:
weights_max_rentability = max_rentability(mean_returns, cov_returns,risk_free_rate)
p_max_rentability       = performance_portfolio(weights_max_rentability,mean_returns,cov_returns,risk_free_rate)
p_max_rentability       = pd.DataFrame(p_max_rentability).transpose()
p_max_rentability.columns = ["retorns","risk","Isharpe"]
p_max_rentability["Type"] = "Max Rentability"
p_max_rentability["weights"] = str(list(np.around(weights_max_rentability,2)*100))
p_max_rentability

retorns      risk   Isharpe             Type                      weights
0  0.084327  0.161887  0.335587  Max Rentability  [100.0, 0.0, 0.0, 0.0, 0.0]

In [13]:
weights_max_sharpe = max_sharpe_ratio(mean_returns, cov_returns, risk_free_rate)

p_max_sharpe = performance_portfolio(weights_max_sharpe,mean_returns,cov_returns,risk_free_rate)
p_max_sharpe = pd.DataFrame(p_max_sharpe).transpose()
p_max_sharpe.columns = ["retorns","risk","Isharpe"]
p_max_sharpe["Type"] = "Max Sharpe Index"
p_max_sharpe["weights"] = str(list(np.around(weights_max_sharpe,2)*100) )
p_max_sharpe

retorns      risk   Isharpe              Type                      weights
0  0.067026  0.027771  1.333245  Max Sharpe Index  [0.0, 0.0, 0.0, 11.0, 89.0]

In [14]:
weights_min_variance = min_variance(mean_returns,cov_returns)
p_min_variance = performance_portfolio(weights_min_variance,mean_returns,cov_returns,risk_free_rate)
p_min_variance = pd.DataFrame(p_min_variance).transpose()
p_min_variance.columns = ["retorns","risk","Isharpe"]
p_min_variance["Type"] = "Min Variance"
p_min_variance["weights"] = str(list(np.around(weights_min_variance,2)*100))
p_min_variance

retorns     risk   Isharpe          Type                     weights
0  0.066371  0.02744  1.325483  Min Variance  [1.0, 0.0, 0.0, 0.0, 99.0]

In [15]:
returns_range = np.arange(mean_returns.min(),mean_returns.max(),0.001)
means , stds, sharpe = np.column_stack(
    [performance_portfolio(
        w,mean_returns,cov_returns,risk_free_rate) for w in efficient_frontier(mean_returns,cov_returns,returns_range) ])
frontier_performance = pd.DataFrame(data=(means,stds,sharpe)).transpose()
frontier_performance.columns = ["retorns","risk","Isharpe"]
frontier_performance["Type"] = "Frontier"
frontier_performance["weights"] = np.nan

In [16]:
data_frontier_efficient = pd.concat([other_portfolios,frontier_performance,p_min_variance,p_max_sharpe,p_max_rentability])
data_frontier_efficient = data_frontier_efficient.reset_index(drop = True)
data_frontier_efficient

retorns      risk   Isharpe              Type  \
0      0.074732  0.074255  0.602413            Others   
1      0.078032  0.103809  0.462692            Others   
2      0.073370  0.059368  0.730528            Others   
3      0.076414  0.082201  0.564646            Others   
4      0.075304  0.079520  0.569715            Others   
...         ...       ...       ...               ...   
10017  0.083253  0.148513  0.358573          Frontier   
10018  0.084253  0.160959  0.337060          Frontier   
10019  0.066371  0.027440  1.325483      Min Variance   
10020  0.067026  0.027771  1.333245  Max Sharpe Index   
10021  0.084327  0.161887  0.335587   Max Rentability   

                           weights  
0                              NaN  
1                              NaN  
2                              NaN  
3                              NaN  
4                              NaN  
...                            ...  
10017                          NaN  
10018                          NaN  
10019   [1.0, 0.0, 0.0, 0.0, 99.0]  
10020  [0.0, 0.0, 0.0, 11.0, 89.0]  
10021  [100.0, 0.0, 0.0, 0.0, 0.0]  

[10022 rows x 5 columns]

#### CML =    E[R] = rf + Isharpe * s

In [17]:
graph_frontier_efficient = data_frontier_efficient.plot.scatter(x = "risk",y="retorns", 
                                                    color = "Type",title = "Efficient Frontier Graph -- Retorns vs. risk ")
graph_frontier_efficient 


max_isharpe = p_max_sharpe["Isharpe"].values

rs  = np.arange(risk_free_rate,mean_returns.max(),0.01)  #rentability range
ss  = lambda i: (i-risk_free_rate)/max_isharpe  #CML inverse Function

graph_frontier_efficient.add_trace(
    go.Scatter(
        x=ss(rs),
        y=rs,
        mode="lines",
        line=go.scatter.Line(color="green"),
        showlegend=True,
        name = "Capital Market Line"
    )
)
graph_frontier_efficient.show()

In [18]:
summary_info = pd.concat([p_max_sharpe,p_max_rentability, p_min_variance])
summary_info = summary_info.set_index("Type")
summary_info["retorns"] = summary_info["retorns"]*100
summary_info["risk"] = summary_info["risk"]*100
summary_info.columns = ["Retorns in %","Risk in %", "Sharpe Index","Weights assets in %"]
summary_info

Retorns in %  Risk in %  Sharpe Index  \
Type                                                      
Max Sharpe Index      6.702608   2.777140      1.333245   
Max Rentability       8.432716  16.188683      0.335587   
Min Variance          6.637099   2.743980      1.325483   

                          Weights assets in %  
Type                                           
Max Sharpe Index  [0.0, 0.0, 0.0, 11.0, 89.0]  
Max Rentability   [100.0, 0.0, 0.0, 0.0, 0.0]  
Min Variance       [1.0, 0.0, 0.0, 0.0, 99.0]

In [20]:
summary_info.to_html("sumarry_portfolio_info.html")